In [9]:
import numpy as np
import cv2
import matplotlib.pyplot as plt
import os
from tqdm import tqdm

### Leaf segmentation

In [10]:
def preprocess_image(image, target_size=(640, 640)):
    """Resize image for faster processing."""
    h, w = image.shape[:2]
    
    if max(h, w) > target_size[0]:  # Resize only if larger
        image = cv2.resize(image, target_size, interpolation=cv2.INTER_AREA)
    
    return image

In [11]:
def refine_mask(mask):
    """Refine the mask using morphology and keep only the largest contour."""
    kernel = np.ones((5, 5), np.uint8)
    
    # Fill small holes inside the leaf
    mask_closed = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    
    # Remove small noise
    mask_opened = cv2.morphologyEx(mask_closed, cv2.MORPH_OPEN, kernel, iterations=2)
    
    # Find the largest contour (assumed to be the leaf)
    contours, _ = cv2.findContours(mask_opened, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    
    if contours:
        largest_contour = max(contours, key=cv2.contourArea)
        mask_filtered = np.zeros_like(mask_opened)
        cv2.drawContours(mask_filtered, [largest_contour], -1, 255, thickness=cv2.FILLED)
    else:
        mask_filtered = mask_opened

    return mask_filtered

In [12]:
def hsv_background_removal(image):
    """Use HSV thresholding to remove non-green regions."""
    hsv = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)

    # Define green color range
    lower_green = np.array([30, 40, 40])  # Adjust if needed
    upper_green = np.array([90, 255, 255])

    # Create mask for green areas
    green_mask = cv2.inRange(hsv, lower_green, upper_green)

    return green_mask

In [13]:
def grabcut_segmentation(image):
    """Perform GrabCut segmentation with fewer iterations."""
    mask = np.zeros(image.shape[:2], np.uint8)
    
    # Define bounding box (adjust manually if needed)
    height, width = image.shape[:2]
    bbox = (int(0.1 * width), int(0.2 * height), int(0.8 * width), int(0.6 * height))

    bgd_model = np.zeros((1, 65), np.float64)
    fgd_model = np.zeros((1, 65), np.float64)

    cv2.grabCut(image, mask, bbox, bgd_model, fgd_model, 2, cv2.GC_INIT_WITH_RECT)  # Reduced iterations to 2
    
    # Convert mask to binary
    mask_bin = np.where((mask == 2) | (mask == 0), 0, 1).astype("uint8")

    return mask_bin * 255

In [14]:
def hybrid_segmentation(image):
    """Combine GrabCut and HSV filtering."""
    grabcut_mask = grabcut_segmentation(image)
    hsv_mask = hsv_background_removal(image)

    # Combine both masks
    combined_mask = cv2.bitwise_and(grabcut_mask, hsv_mask)

    # Refine mask
    refined_mask = refine_mask(combined_mask)

    # Apply mask to image
    segmented_leaf = image * (refined_mask[:, :, np.newaxis] // 255)

    return refined_mask, segmented_leaf

In [15]:
def process_dataset(input_folder, output_folder):
    """Processes all images recursively using the optimized segmentation pipeline."""
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    image_extensions = (".jpg", ".jpeg", ".png", ".bmp", ".tiff")
    
    for root, dirs, files in os.walk(input_folder):
        for image_name in tqdm(files, desc=f"Processing Images in {root}"):
            if not image_name.lower().endswith(image_extensions):
                continue
            
            image_path = os.path.join(root, image_name)
            
            # Rebuild the same relative path for output
            rel_path = os.path.relpath(root, input_folder)
            save_folder = os.path.join(output_folder, rel_path)
            if not os.path.exists(save_folder):
                os.makedirs(save_folder)
            
            output_path = os.path.join(save_folder, image_name)
            
            image = cv2.imread(image_path)
            if image is None:
                print(f"Skipping {image_name}, unable to read.")
                continue
            
            image = preprocess_image(image)
            _, segmented_leaf = hybrid_segmentation(image)
            cv2.imwrite(output_path, segmented_leaf)

    print(f"Processed all images. Saved to {output_folder}")


In [16]:
if __name__ == "__main__":
    input_folder = r"D:\Workplace\.SPRING2025\res\test"
    output_folder = r"D:\Workplace\.SPRING2025\res\masked"
    process_dataset(input_folder, output_folder)    


Processing Images in D:\Workplace\.SPRING2025\res\test: 100%|██████████| 185/185 [03:37<00:00,  1.18s/it]

Processed all images. Saved to D:\Workplace\.SPRING2025\res\masked


In [4]:
import numpy as np
import cv2
import os
from tqdm import tqdm

def preprocess_image(image, target_size=(640, 640)):
    h, w = image.shape[:2]
    if max(h, w) > target_size[0]: 
        image = cv2.resize(image, target_size, interpolation=cv2.INTER_AREA)
    return image

def grabcut_segmentation(image):
    mask = np.zeros(image.shape[:2], np.uint8)
    height, width = image.shape[:2]
    bbox = (int(0.05 * width), int(0.05 * height), int(0.9 * width), int(0.9 * height))

    bgd_model = np.zeros((1, 65), np.float64)
    fgd_model = np.zeros((1, 65), np.float64)

    cv2.grabCut(image, mask, bbox, bgd_model, fgd_model, 5, cv2.GC_INIT_WITH_RECT)
    mask_bin = np.where((mask == 2) | (mask == 0), 0, 1).astype("uint8")

    return mask_bin * 255  

def refine_mask(mask):
    kernel = np.ones((5, 5), np.uint8)
    mask = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    mask = cv2.morphologyEx(mask, cv2.MORPH_OPEN, kernel, iterations=2)

    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if contours:
        largest_contour = max(contours, key=cv2.contourArea)
        final_mask = np.zeros_like(mask)
        cv2.drawContours(final_mask, [largest_contour], -1, 255, thickness=cv2.FILLED)
    else:
        final_mask = mask  
    return final_mask

def segment_leaf(image):
    grabcut_mask = grabcut_segmentation(image)
    refined_mask = refine_mask(grabcut_mask)
    return refined_mask

def apply_mask(image, mask):
    return image * (mask[:, :, np.newaxis] // 255)

def create_yolo_segmentation_annotation(mask, image_shape, save_path, class_id=0):
    """Generate YOLOv11-seg polygon annotation from the mask."""
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    if not contours:
        return

    largest_contour = max(contours, key=cv2.contourArea)
    img_h, img_w = image_shape[:2]

    # Flatten the contour points
    polygon = largest_contour.reshape(-1, 2)

    # Normalize points
    normalized_polygon = []
    for x, y in polygon:
        norm_x = x / img_w
        norm_y = y / img_h
        normalized_polygon.extend([norm_x, norm_y])

    # Optional: limit number of points (YOLOv11-seg can handle a lot but still better to control it)
    # normalized_polygon = normalized_polygon[:50 * 2]  # Keep first 50 points if needed

    # Save as .txt file
    with open(save_path, "w") as f:
        f.write(f"{class_id} " + " ".join([f"{p:.6f}" for p in normalized_polygon]) + "\n")

def process_dataset(input_folder, output_folder):
    """Process the dataset using GrabCut segmentation and create annotations."""
    images_folder = os.path.join(output_folder, "images")
    labels_folder = os.path.join(output_folder, "labels")

    # Create output folders if they don't exist
    os.makedirs(images_folder, exist_ok=True)
    os.makedirs(labels_folder, exist_ok=True)

    image_extensions = (".jpg", ".jpeg", ".png", ".bmp", ".tiff")

    # Walk through each folder (Train, Test, etc.) within the input folder
    for root, dirs, files in os.walk(input_folder):
        # Only process folders (Train, Test, Val, etc.)
        for folder in dirs:
            folder_path = os.path.join(root, folder)
            images_folder_path = os.path.join(images_folder, folder)
            labels_folder_path = os.path.join(labels_folder, folder)

            # Create subfolders for images and labels
            os.makedirs(images_folder_path, exist_ok=True)
            os.makedirs(labels_folder_path, exist_ok=True)

            for image_name in tqdm(os.listdir(folder_path), desc=f"Processing {folder}"):
                if not image_name.lower().endswith(image_extensions):
                    continue

                image_path = os.path.join(folder_path, image_name)

                image = cv2.imread(image_path)
                if image is None:
                    print(f"Skipping {image_name}, unable to read.")
                    continue

                image = preprocess_image(image)
                mask = segment_leaf(image)
                segmented_leaf = apply_mask(image, mask)

                # Save the segmented image
                save_image_path = os.path.join(images_folder_path, image_name)
                cv2.imwrite(save_image_path, segmented_leaf)

                # Create annotation file (bounding box from mask)
                label_path = os.path.join(labels_folder_path, os.path.splitext(image_name)[0] + ".txt")
                create_yolo_segmentation_annotation(mask, image.shape, label_path)

    print(f"Finished processing. Images saved to {images_folder}, labels saved to {labels_folder}")
if __name__ == "__main__":
    input_folder = r"D:\Workplace\.SPRING2025\res\Final_unmasked"
    output_folder = r"D:\Workplace\.SPRING2025\res\masked"
    process_dataset(input_folder, output_folder)


Processing Cherry_(including_sour)___healthy: 100%|██████████| 854/854 [02:26<00:00,  5.84it/s]
Processing Cherry_(including_sour)___Powdery_mildew: 100%|██████████| 1052/1052 [03:41<00:00,  4.74it/s]
Processing Grape___healthy: 100%|██████████| 1329/1329 [19:14<00:00,  1.15it/s] 
Processing Grape___Leaf_blight_(Isariopsis_Leaf_Spot): 100%|██████████| 1076/1076 [05:53<00:00,  3.04it/s]
Processing Strawberry___Leaf_scorch: 100%|██████████| 1109/1109 [05:37<00:00,  3.28it/s]

Finished processing. Images saved to D:\Workplace\.SPRING2025\res\masked\images, labels saved to D:\Workplace\.SPRING2025\res\masked\labels


In [2]:
import os
import random
import shutil
from tqdm import tqdm

def get_all_images(root_folder):
    """Collect all image paths, distinguishing simple and complex cases."""
    image_extensions = (".jpg", ".jpeg", ".png", ".bmp", ".tiff")
    all_images = []
    
    # Walk through each subfolder (e.g., Apple_Apple_scab)
    for subfolder in os.listdir(root_folder):
        subfolder_path = os.path.join(root_folder, subfolder)
        if not os.path.isdir(subfolder_path):
            continue
            
        # Check for a 'Complex' subfolder
        complex_folder = os.path.join(subfolder_path, "bad")
        
        # Simple case images (directly in subfolder)
        for image_name in os.listdir(subfolder_path):
            image_path = os.path.join(subfolder_path, image_name)
            if os.path.isfile(image_path) and image_name.lower().endswith(image_extensions):
                all_images.append(image_path)
        
        # Complex case images (in Complex subfolder)
        if os.path.isdir(complex_folder):
            for image_name in os.listdir(complex_folder):
                image_path = os.path.join(complex_folder, image_name)
                if image_name.lower().endswith(image_extensions):
                    all_images.append(image_path)
    
    return all_images

def select_random_images(all_images, percentage=0.25):
    """Randomly select a percentage of images."""
    num_images = len(all_images)
    num_to_select = int(num_images * percentage)
    selected_images = random.sample(all_images, num_to_select)
    return selected_images

def copy_selected_images(selected_images, root_folder, output_folder):
    """Copy selected images to a new folder, preserving the folder structure."""
    os.makedirs(output_folder, exist_ok=True)
    
    for image_path in tqdm(selected_images, desc="Copying images"):
        # Get the relative path from the root (e.g., Apple_Apple_scab/Complex/image.jpg)
        relative_path = os.path.relpath(image_path, root_folder)
        # Construct the destination path
        dest_path = os.path.join(output_folder, relative_path)
        # Create the destination directory if it doesn't exist
        os.makedirs(os.path.dirname(dest_path), exist_ok=True)
        # Copy the image
        shutil.copy2(image_path, dest_path)

def main():
    root_folder = r"D:\Workplace\.SPRING2025\res\Final_unmasked"
    output_folder = r"D:\Workplace\.SPRING2025\res\Final_unmasked_selected"
    
    # Step 1: Collect all images
    print("Collecting images...")
    all_images = get_all_images(root_folder)
    
    print(f"Total images: {len(all_images)}")
    
    # Step 2: Randomly select 25% of images
    print("Selecting 25% of images...")
    selected_images = select_random_images(all_images, percentage=0.25)
    
    # Step 3: Copy the selected images to the new folder
    print(f"Copying selected images to {output_folder}")
    copy_selected_images(selected_images, root_folder, output_folder)
    
    print(f"Copied {len(selected_images)} images. Done!")

if __name__ == "__main__":
    main()

Total images: 20835
Selecting 25% of images...
Copying selected images to D:\Workplace\.SPRING2025\res\Final_unmasked_selected


Copying images: 100%|██████████| 5208/5208 [00:26<00:00, 198.79it/s]

Copied 5208 images. Done!


In [5]:
import torch
import torchvision
from segment_anything import SamPredictor, sam_model_registry

print(torch.__version__)  # E.g., 2.4.1
print(torchvision.__version__)  # Should match, e.g., 0.19.1
print(torch.cuda.is_available())  # Should match your PyTorch installation (True if CUDA is set up)

2.6.0+cpu
0.21.0+cpu
False


In [7]:
import requests

url = "https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth"
filename = "sam_vit_h_4b8939.pth"

print(f"Downloading {filename}...")
response = requests.get(url, stream=True)
with open(filename, "wb") as f:
    for chunk in response.iter_content(chunk_size=8192):
        if chunk:
            f.write(chunk)
print("Download complete.")

Download complete.


In [14]:
import os
import numpy as np
import cv2
from tqdm import tqdm
from segment_anything import SamPredictor, sam_model_registry
import torch

# Initialize SAM
sam_checkpoint = "sam_vit_h_4b8939.pth"
model_type = "vit_h"
sam = sam_model_registry[model_type](checkpoint=sam_checkpoint)
if torch.cuda.is_available():
    sam.to(device="cuda")
predictor = SamPredictor(sam)

def preprocess_image(image, target_size=(640, 640)):
    h, w = image.shape[:2]
    if max(h, w) > target_size[0]: 
        image = cv2.resize(image, target_size, interpolation=cv2.INTER_AREA)
    return image

def get_leaf_center(image):
    """Detect the leaf using color-based segmentation and return its center as a point prompt."""
    # Convert to HSV color space
    hsv = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
    
    # Define range for green color (adjust as needed for diseased leaves)
    lower_green = np.array([25, 40, 40])  # Hue: 25-80 for green, adjusted for diseased areas
    upper_green = np.array([80, 255, 255])
    mask = cv2.inRange(hsv, lower_green, upper_green)
    
    # Apply morphological operations to clean up the mask
    kernel = np.ones((5, 5), np.uint8)
    mask = cv2.morphologyEx(mask, cv2.MORPH_OPEN, kernel, iterations=2)
    mask = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    
    # Find contours
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not contours:
        # Fallback: Use the image center
        height, width = image.shape[:2]
        return [width // 2, height // 2]
    
    # Select the largest contour (most likely the main leaf)
    largest_contour = max(contours, key=cv2.contourArea)
    
    # Compute the centroid
    M = cv2.moments(largest_contour)
    if M["m00"] == 0:
        height, width = image.shape[:2]
        return [width // 2, height // 2]
    cx = int(M["m10"] / M["m00"])
    cy = int(M["m01"] / M["m00"])
    
    return [cx, cy]

def sam_segmentation(image, point):
    """Segment the image using SAM with a point prompt."""
    predictor.set_image(image)
    masks, scores, _ = predictor.predict(
        point_coords=np.array([point]),
        point_labels=np.array([1]),  # 1 for foreground
        multimask_output=False
    )
    best_mask = masks[np.argmax(scores)]
    return (best_mask * 255).astype(np.uint8)

def refine_mask(mask):
    kernel = np.ones((5, 5), np.uint8)
    mask = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    mask = cv2.morphologyEx(mask, cv2.MORPH_OPEN, kernel, iterations=2)
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if contours:
        largest_contour = max(contours, key=cv2.contourArea)
        final_mask = np.zeros_like(mask)
        cv2.drawContours(final_mask, [largest_contour], -1, 255, thickness=cv2.FILLED)
    else:
        final_mask = mask
    return final_mask

def segment_leaf_complex(image):
    point = get_leaf_center(image)
    sam_mask = sam_segmentation(image, point)
    refined_mask = refine_mask(sam_mask)
    return refined_mask

def apply_mask(image, mask):
    return image * (mask[:, :, np.newaxis] // 255)

def create_yolo_segmentation_annotation(mask, image_shape, save_path, class_id=0):
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not contours:
        return
    largest_contour = max(contours, key=cv2.contourArea)
    epsilon = 0.005 * cv2.arcLength(largest_contour, True)
    approx_contour = cv2.approxPolyDP(largest_contour, epsilon, True)
    img_h, img_w = image_shape[:2]
    polygon = approx_contour.reshape(-1, 2)
    normalized_polygon = []
    for x, y in polygon:
        norm_x = x / img_w
        norm_y = y / img_h
        normalized_polygon.extend([norm_x, norm_y])
    with open(save_path, "w") as f:
        f.write(f"{class_id} " + " ".join([f"{p:.6f}" for p in normalized_polygon]) + "\n")

def process_complex_images(input_folder, output_folder, complex_subfolder_name="bad"):
    if not os.path.exists(input_folder):
        raise FileNotFoundError(f"Input folder {input_folder} does not exist.")
    print(f"Accessing input folder: {input_folder}")
    print(f"Subfolders found: {os.listdir(input_folder)}")
    images_folder = os.path.join(output_folder, "images")
    labels_folder = os.path.join(output_folder, "labels")
    os.makedirs(images_folder, exist_ok=True)
    os.makedirs(labels_folder, exist_ok=True)
    image_extensions = (".jpg", ".jpeg", ".png", ".bmp", ".tiff")
    total_images_processed = 0
    for subfolder in os.listdir(input_folder):
        subfolder_path = os.path.join(input_folder, subfolder)
        if not os.path.isdir(subfolder_path):
            print(f"Skipping {subfolder}, not a directory.")
            continue
        complex_folder = os.path.join(subfolder_path, complex_subfolder_name)
        if not os.path.isdir(complex_folder):
            print(f"No {complex_subfolder_name} subfolder found in {subfolder}.")
            continue
        print(f"Found {complex_subfolder_name} subfolder in {subfolder}: {complex_folder}")
        images_in_complex = [f for f in os.listdir(complex_folder) if f.lower().endswith(image_extensions)]
        print(f"Images in {complex_folder}: {len(images_in_complex)}")
        if not images_in_complex:
            print(f"No images found in {complex_folder}.")
            continue
        images_folder_path = os.path.join(images_folder, subfolder, complex_subfolder_name)
        labels_folder_path = os.path.join(labels_folder, subfolder, complex_subfolder_name)
        os.makedirs(images_folder_path, exist_ok=True)
        os.makedirs(labels_folder_path, exist_ok=True)
        for image_name in tqdm(images_in_complex, desc=f"Processing {subfolder}/{complex_subfolder_name}"):
            image_path = os.path.join(complex_folder, image_name)
            image = cv2.imread(image_path)
            if image is None:
                print(f"Skipping {image_name}, unable to read.")
                continue
            image = preprocess_image(image)
            mask = segment_leaf_complex(image)
            segmented_leaf = apply_mask(image, mask)
            save_image_path = os.path.join(images_folder_path, image_name)
            cv2.imwrite(save_image_path, segmented_leaf)
            label_path = os.path.join(labels_folder_path, os.path.splitext(image_name)[0] + ".txt")
            create_yolo_segmentation_annotation(mask, image.shape, label_path)
            total_images_processed += 1
    print(f"Finished processing. Total images processed: {total_images_processed}")
    print(f"Images saved to {images_folder}, labels saved to {labels_folder}")

if __name__ == "__main__":
    input_folder = r"D:\Workplace\.SPRING2025\res\Final_unmasked"
    output_folder = r"D:\Workplace\.SPRING2025\res\masked_selected"
    complex_subfolder_name = "bad"
    process_complex_images(input_folder, output_folder, complex_subfolder_name)

Accessing input folder: D:\Workplace\.SPRING2025\res\Final_unmasked
Subfolders found: ['Apple___Apple_scab', 'Apple___Black_rot', 'Apple___Cedar_apple_rust', 'Apple___healthy', 'Cherry_(including_sour)___healthy', 'Cherry_(including_sour)___Powdery_mildew', 'Grape Brown_Spot', 'Grape Downy_Mildew', 'Grape Mites_Disease', 'Grape___Black_rot', 'Grape___Esca_(Black_Measles)', 'Grape___healthy', 'Grape___Leaf_blight_(Isariopsis_Leaf_Spot)', 'Mango Anthracnose', 'Mango Bacterial Canker', 'Mango Cutting Weevil', 'Mango Die Back', 'Mango Gall Midge', 'Mango Healthy', 'Mango Powdery Mildew', 'Mango Sooty Mould', 'Peach___Bacterial_spot', 'Peach___healthy', 'Strawberry___healthy', 'Strawberry___Leaf_scorch']
Found bad subfolder in Apple___Apple_scab: D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___Apple_scab\bad
Images in D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___Apple_scab\bad: 78


Processing Apple___Apple_scab/bad: 100%|██████████| 78/78 [43:42<00:00, 33.62s/it]


No bad subfolder found in Apple___Black_rot.
Found bad subfolder in Apple___Cedar_apple_rust: D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___Cedar_apple_rust\bad
Images in D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___Cedar_apple_rust\bad: 84


Processing Apple___Cedar_apple_rust/bad: 100%|██████████| 84/84 [42:17<00:00, 30.20s/it] 


Found bad subfolder in Apple___healthy: D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___healthy\bad
Images in D:\Workplace\.SPRING2025\res\Final_unmasked\Apple___healthy\bad: 65


...

No bad subfolder found in Grape___Leaf_blight_(Isariopsis_Leaf_Spot).
Found bad subfolder in Mango Anthracnose: D:\Workplace\.SPRING2025\res\Final_unmasked\Mango Anthracnose\bad
Images in D:\Workplace\.SPRING2025\res\Final_unmasked\Mango Anthracnose\bad: 62


Processing Mango Anthracnose/bad: 100%|██████████| 62/62 [29:53<00:00, 28.93s/it]


No bad subfolder found in Mango Bacterial Canker.
No bad subfolder found in Mango Cutting Weevil.
No bad subfolder found in Mango Die Back.
No bad subfolder found in Mango Gall Midge.
No bad subfolder found in Mango Healthy.
No bad subfolder found in Mango Powdery Mildew.
No bad subfolder found in Mango Sooty Mould.
No bad subfolder found in Peach___Bacterial_spot.
No bad subfolder found in Peach___healthy.
Found bad subfolder in Strawberry___healthy: D:\Workplace\.SPRING2025\res\Final_unmasked\Strawberry___healthy\bad
Images in D:\Workplace\.SPRING2025\res\Final_unmasked\Strawberry___healthy\bad: 184


Processing Strawberry___healthy/bad: 100%|██████████| 184/184 [1:52:47<00:00, 36.78s/it]

No bad subfolder found in Strawberry___Leaf_scorch.
Finished processing. Total images processed: 588
Images saved to D:\Workplace\.SPRING2025\res\masked_selected\images, labels saved to D:\Workplace\.SPRING2025\res\masked_selected\labels


In [6]:
import os
import numpy as np
import cv2
from tqdm import tqdm
from segment_anything import SamPredictor, sam_model_registry
import torch
import time

# Initialize SAM with device logging
sam_checkpoint = "sam_vit_l_0b3195.pth"  # Using ViT-L as a compromise
model_type = "vit_l"
sam = sam_model_registry[model_type](checkpoint=sam_checkpoint)

# Check if GPU is available and move model to the appropriate device
if torch.cuda.is_available():
    sam.to(device="cuda")
    device = "cuda"
    print("GPU is available. SAM model moved to GPU (CUDA).")
    print(f"Number of GPUs available: {torch.cuda.device_count()}")
    print(f"Current GPU device: {torch.cuda.current_device()}")
    print(f"GPU name: {torch.cuda.get_device_name(torch.cuda.current_device())}")
else:
    device = "cpu"
    print("No GPU available. SAM model will run on CPU.")

predictor = SamPredictor(sam)

def preprocess_image(image, target_size=(512, 512)):
    h, w = image.shape[:2]
    if max(h, w) > target_size[0]: 
        image = cv2.resize(image, target_size, interpolation=cv2.INTER_AREA)
    return image

def get_leaf_center(image):
    hsv = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
    lower_green = np.array([20, 30, 30])  # Adjusted for better leaf detection
    upper_green = np.array([100, 255, 255])
    mask = cv2.inRange(hsv, lower_green, upper_green)
    kernel = np.ones((5, 5), np.uint8)
    mask = cv2.morphologyEx(mask, cv2.MORPH_OPEN, kernel, iterations=2)
    mask = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not contours:
        height, width = image.shape[:2]
        return [width // 2, height // 2]
    min_contour_area = 500
    valid_contours = [cnt for cnt in contours if cv2.contourArea(cnt) > min_contour_area]
    if not valid_contours:
        height, width = image.shape[:2]
        return [width // 2, height // 2]
    largest_contour = max(valid_contours, key=cv2.contourArea)
    M = cv2.moments(largest_contour)
    if M["m00"] == 0:
        height, width = image.shape[:2]
        return [width // 2, height // 2]
    cx = int(M["m10"] / M["m00"])
    cy = int(M["m01"] / M["m00"])
    return [cx, cy]

def sam_segmentation(image, point):
    predictor.set_image(image)
    print(f"Running SAM inference on device: {device}")
    start_time = time.time()
    masks, scores, _ = predictor.predict(
        point_coords=np.array([point]),
        point_labels=np.array([1]),
        multimask_output=False
    )
    end_time = time.time()
    print(f"SAM inference took {end_time - start_time:.2f} seconds")
    best_mask = masks[np.argmax(scores)]
    return (best_mask * 255).astype(np.uint8)

def refine_mask(mask):
    kernel = np.ones((5, 5), np.uint8)
    mask = cv2.morphologyEx(mask, cv2.MORPH_CLOSE, kernel, iterations=2)
    mask = cv2.morphologyEx(mask, cv2.MORPH_OPEN, kernel, iterations=2)
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if contours:
        largest_contour = max(contours, key=cv2.contourArea)
        final_mask = np.zeros_like(mask)
        cv2.drawContours(final_mask, [largest_contour], -1, 255, thickness=cv2.FILLED)
    else:
        final_mask = mask
    return final_mask

def segment_leaf(image):
    point = get_leaf_center(image)
    sam_mask = sam_segmentation(image, point)
    refined_mask = refine_mask(sam_mask)
    return refined_mask

def apply_mask(image, mask):
    return image * (mask[:, :, np.newaxis] // 255)

def create_yolo_segmentation_annotation(mask, image_shape, save_path, class_id=0):
    contours, _ = cv2.findContours(mask, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    if not contours:
        return
    largest_contour = max(contours, key=cv2.contourArea)
    epsilon = 0.005 * cv2.arcLength(largest_contour, True)
    approx_contour = cv2.approxPolyDP(largest_contour, epsilon, True)
    img_h, img_w = image_shape[:2]
    polygon = approx_contour.reshape(-1, 2)
    normalized_polygon = []
    for x, y in polygon:
        norm_x = x / img_w
        norm_y = y / img_h
        normalized_polygon.extend([norm_x, norm_y])
    with open(save_path, "w") as f:
        f.write(f"{class_id} " + " ".join([f"{p:.6f}" for p in normalized_polygon]) + "\n")

def process_non_bad_images(input_folder, output_folder, ignore_subfolder_name="bad"):
    if not os.path.exists(input_folder):
        raise FileNotFoundError(f"Input folder {input_folder} does not exist.")
    print(f"Accessing input folder: {input_folder}")
    print(f"Subfolders found: {os.listdir(input_folder)}")
    images_folder = os.path.join(output_folder, "images")
    labels_folder = os.path.join(output_folder, "labels")
    os.makedirs(images_folder, exist_ok=True)
    os.makedirs(labels_folder, exist_ok=True)
    image_extensions = (".jpg", ".jpeg", ".png", ".bmp", ".tiff")
    total_images_processed = 0

    for subfolder in os.listdir(input_folder):
        subfolder_path = os.path.join(input_folder, subfolder)
        if not os.path.isdir(subfolder_path):
            print(f"Skipping {subfolder}, not a directory.")
            continue

        # Process images directly in the disease folder
        images_in_subfolder = [f for f in os.listdir(subfolder_path) if f.lower().endswith(image_extensions)]
        if images_in_subfolder:
            print(f"Images directly in {subfolder}: {len(images_in_subfolder)}")
            images_folder_path = os.path.join(images_folder, subfolder)
            labels_folder_path = os.path.join(labels_folder, subfolder)
            os.makedirs(images_folder_path, exist_ok=True)
            os.makedirs(labels_folder_path, exist_ok=True)
            for image_name in tqdm(images_in_subfolder, desc=f"Processing {subfolder}/direct"):
                image_path = os.path.join(subfolder_path, image_name)
                image = cv2.imread(image_path)
                if image is None:
                    print(f"Skipping {image_name}, unable to read.")
                    continue
                image = preprocess_image(image)
                mask = segment_leaf(image)
                segmented_leaf = apply_mask(image, mask)
                save_image_path = os.path.join(images_folder_path, image_name)
                cv2.imwrite(save_image_path, segmented_leaf)
                label_path = os.path.join(labels_folder_path, os.path.splitext(image_name)[0] + ".txt")
                create_yolo_segmentation_annotation(mask, image.shape, label_path)
                total_images_processed += 1

        # Process images in subfolders, excluding the 'bad' subfolder
        for sub_subfolder in os.listdir(subfolder_path):
            sub_subfolder_path = os.path.join(subfolder_path, sub_subfolder)
            if not os.path.isdir(sub_subfolder_path) or sub_subfolder == ignore_subfolder_name:
                if sub_subfolder == ignore_subfolder_name:
                    print(f"Ignoring {sub_subfolder} subfolder in {subfolder}.")
                continue
            print(f"Found subfolder {sub_subfolder} in {subfolder}: {sub_subfolder_path}")
            images_in_sub_subfolder = [f for f in os.listdir(sub_subfolder_path) if f.lower().endswith(image_extensions)]
            print(f"Images in {sub_subfolder_path}: {len(images_in_sub_subfolder)}")
            if not images_in_sub_subfolder:
                print(f"No images found in {sub_subfolder_path}.")
                continue
            images_folder_path = os.path.join(images_folder, subfolder, sub_subfolder)
            labels_folder_path = os.path.join(labels_folder, subfolder, sub_subfolder)
            os.makedirs(images_folder_path, exist_ok=True)
            os.makedirs(labels_folder_path, exist_ok=True)
            for image_name in tqdm(images_in_sub_subfolder, desc=f"Processing {subfolder}/{sub_subfolder}"):
                image_path = os.path.join(sub_subfolder_path, image_name)
                image = cv2.imread(image_path)
                if image is None:
                    print(f"Skipping {image_name}, unable to read.")
                    continue
                image = preprocess_image(image)
                mask = segment_leaf(image)
                segmented_leaf = apply_mask(image, mask)
                save_image_path = os.path.join(images_folder_path, image_name)
                cv2.imwrite(save_image_path, segmented_leaf)
                label_path = os.path.join(labels_folder_path, os.path.splitext(image_name)[0] + ".txt")
                create_yolo_segmentation_annotation(mask, image.shape, label_path)
                total_images_processed += 1

    print(f"Finished processing. Total images processed: {total_images_processed}")
    print(f"Images saved to {images_folder}, labels saved to {labels_folder}")

if __name__ == "__main__":
    input_folder = r"D:\Workplace\.SPRING2025\res\Final_unmasked"
    output_folder = r"D:\Workplace\.SPRING2025\res\masked_good"
    ignore_subfolder_name = "bad"
    process_non_bad_images(input_folder, output_folder, ignore_subfolder_name)

GPU is available. SAM model moved to GPU (CUDA).
Number of GPUs available: 1
Current GPU device: 0
GPU name: NVIDIA GeForce RTX 3050 Laptop GPU
Accessing input folder: D:\Workplace\.SPRING2025\res\Final_unmasked
Subfolders found: ['Apple___Apple_scab', 'Apple___Black_rot', 'Apple___Cedar_apple_rust', 'Apple___healthy', 'Cherry_(including_sour)___healthy', 'Cherry_(including_sour)___Powdery_mildew', 'Grape Brown_Spot', 'Grape Downy_Mildew', 'Grape Mites_Disease', 'Grape___Black_rot', 'Grape___Esca_(Black_Measles)', 'Grape___healthy', 'Grape___Leaf_blight_(Isariopsis_Leaf_Spot)', 'Mango Bacterial Canker', 'Mango Cutting Weevil', 'Mango Die Back', 'Mango Gall Midge', 'Mango Healthy', 'Mango Powdery Mildew', 'Mango Sooty Mould', 'Peach___Bacterial_spot', 'Peach___healthy', 'Strawberry___healthy', 'Strawberry___Leaf_scorch']
Images directly in Apple___Apple_scab: 639


Processing Apple___Apple_scab/direct:   0%|          | 0/639 [00:00<?, ?it/s]

Running SAM inference on device: cuda


Processing Apple___Apple_scab/direct:   0%|          | 1/639 [00:03<42:15,  3.97s/it]

SAM inference took 0.46 seconds
Running SAM inference on device: cuda


...

SAM inference took 0.55 seconds
Running SAM inference on device: cuda


Processing Strawberry___Leaf_scorch/direct: 100%|█████████▉| 1108/1109 [59:54<00:03,  3.32s/it]

SAM inference took 0.52 seconds
Running SAM inference on device: cuda


Processing Strawberry___Leaf_scorch/direct: 100%|██████████| 1109/1109 [59:57<00:00,  3.24s/it]

SAM inference took 0.55 seconds
Finished processing. Total images processed: 19854
Images saved to D:\Workplace\.SPRING2025\res\masked_good\images, labels saved to D:\Workplace\.SPRING2025\res\masked_good\labels
